# Symbolic Partial Derivative Routine

## Authors: Zach Etienne & Tyler Knowles

## This module contains a routine for computing partial derivatives of a mathematical expression that is written as several subexpressions.

**Notebook Status:** <font color='green'><b> Validated </b></font>

**Validation Notes:** This tutorial notebook has been confirmed to be self-consistent with its corresponding NRPy+ module, as documented [below](#code_validation). Additionally, this notebook has been validated by checking that results are consistent with exact derivative expressions used in the SEOBNRv3_opt approixment of [LALSuite](https://git.ligo.org/lscsoft/lalsuite).

### NRPy+ Source Code for this module: [SEOBNR_Derivative_Routine.py](../edit/SEOBNR/SEOBNR_Derivative_Routine.py)

## Introduction
$$\label{intro}$$

This notebook documents the symbolic partial derivative routine used to generate analytic derivatives of the [SEOBNRv3](https://git.ligo.org/lscsoft/lalsuite) Hamiltonian (documented [here](../Tutorial-SEOBNR_v3_Hamiltonian.ipynb)) and described in [this article](https://arxiv.org/abs/1803.06346).  In general, this notebook takes as input a file of inter-dependent mathematical expressions (in SymPy syntax), a file listing the names of values within those expressions, and a file listing all variables with which to take partial derivatives of each expression.  The output is a text file containing the original expression and those for each partial derivative computation.  The intention is to perform CSE on these expressions to create efficient partial derivative code!

<a id='toc'></a>

# Table of Contents
$$\label{toc}$$

This notebook is organized as follows

1. [Step 1](#initializenrpy): Initialize core Python/NRPy+ modules
1. [Step 2:](#read_expressions) Read in Hamiltonian expressions from `Hamstring.txt`
1. [Step 3:](#list_constants) Specify constants and variables in Hamiltonian expression
1. [Step 4:](#list_free_symbols) Extract free symbols
1. [Step 5:](#convert_to_func) Convert variables to function notation; e.g., `var` goes to `var(xx)`
1. [Step 6:](#differentiate) Differentiate with respect to `xx`
1. [Step 7:](#remove_zeros) Remove derivatives (of constants) that evaluate to zero, simplifying derivative expressions
1. [Step 8:](#partial_derivative) Simplify derivatives with respect to a specific variable
1. [Step 9:](#store_results) Store partial derivatives to SymPy notebook `partial_derivatives.txt-VALIDATION.txt`
1. [Step 10:](#code_validation) Validate against trusted `SEOBNR_Derivative_Routine` NRPy+ module
1. [Step 11:](#latex_pdf_output) Output this notebook to $\LaTeX$-formatted PDF file

<a id='initializenrpy'></a>

# Step 1: Initialize core Python/NRPy+ modules \[Back to [top](#toc)\]
$$\label{initializenrpy}$$

Let's start by importing all the needed modules from Python/NRPy+ and creating the output directory (if it does not already exist):

In [1]:
# Step 1.a: import all needed modules from Python/NRPy+:
import sympy as sp                # SymPy: The Python computer algebra package upon which NRPy+ depends
import os, sys                    # Standard Python modules for multiplatform OS-level functions
from outputC import superfast_uniq, lhrh      # Remove duplicate entries from a Python array; store left- and right-
                                              #   hand sides of mathematical expressions

# Step 1.b: Check for a sufficiently new version of SymPy (for validation)
# Ignore the rc's and b's for release candidates & betas.
sympy_version = sp.__version__.replace('rc', '...').replace('b', '...')
sympy_version_decimal = float(int(sympy_version.split(".")[0]) + int(sympy_version.split(".")[1])/10.0)
if sympy_version_decimal < 1.2:
    print('Error: NRPy+ does not support SymPy < 1.2')
    sys.exit(1)

# Step 1.c: Name of the directory containing the input file
inputdir = "SEOBNR"

<a id='read_expressions'></a>

# Step 2: Read in Hamiltonian expressions from `Hamstring.txt` \[Back to [top](#toc)\]
$$\label{read_expressions}$$

We read in the expressions of which we will compute partial derivatives in a single large string before splitting the string by line (carriage return) and by "=".  Doing so allows us to manipulate the right- and left-hand sides of the expressions appropriately.  We store the left- and right-hand sides in the array `lr`, which consists of `lhrh` arrays with left-hand sides `lhs` and right-hand sides `rhs`.  Note that `Lambda` is a protected keyword in Python, so the variable $\Lambda$ in the Hamiltonian is renamed `Lamb`.

In [2]:
# Step 2.a: Read in expressions as a (single) string
#with open('in_progress/SEOBNR/Hamstring_lite.txt', 'r') as file:#TYLERK
with open(os.path.join(inputdir,'Hamstring.txt'), 'r') as file:
    expressions_as_lines = file.readlines()

# Step 2.b: Create and populate the "lr" array, which separates each line into left- and right-hand sides
#   Each entry is a string of the form lhrh(lhs='',rhs='')
lr = []

for i in range(len(expressions_as_lines)):
    # Ignore lines with 2 or fewer characters and those starting with #
    if len(expressions_as_lines[i]) > 2 and expressions_as_lines[i][0] != "#":
        # Split each line by its equals sign
        split_line = expressions_as_lines[i].split("=")
        # Append the line to "lr", removing spaces, "sp." prefixes, and replacing Lambda->Lamb
        #   (Lambda is a protected keyword):
        lr.append(lhrh(lhs=split_line[0].replace(" ","").replace("Lambda","Lamb"),
                       rhs=split_line[1].replace(" ","").replace("sp.","").replace("Lambda","Lamb")))

# Step 2.c: Separate and sympify right- and left-hand sides into separate arrays
lhss = []
rhss = []
for i in range(len(lr)):
    lhss.append(sp.sympify(lr[i].lhs))
    rhss.append(sp.sympify(lr[i].rhs))

<a id='list_constants'></a>

# Step 3: Specify constants and variables in Hamiltonian expression \[Back to [top](#toc)\]
$$\label{list_constants}$$

We read in and declare as SymPy symbols the constant values; derivatives with respect to these variables will be set to zero.  We then read in the variables with respect to which we want to take derivatives and declare those as SymPy variables as well.

In [3]:
# Step 3.a: Create `input_constants` array and populate with SymPy symbols
m1,m2,tortoise,eta,KK,k0,k1,EMgamma,d1v2,dheffSSv2 = sp.symbols('m1 m2 tortoise eta KK k0 k1 EMgamma d1v2 dheffSSv2',
                                                                real=True)
input_constants = [m1,m2,tortoise,eta,KK,k0,k1,EMgamma,d1v2,dheffSSv2]

# Step 3.b: Create `dynamic_variables` array and populate with SymPy symbols
x,y,z,px,py,pz,s1x,s1y,s1z,s2x,s2y,s2z = sp.symbols('x y z px py pz s1x s1y s1z s2x s2y s2z', real=True)
dynamic_variables = [x,y,z,px,py,pz,s1x,s1y,s1z,s2x,s2y,s2z]

<a id='list_free_symbols'></a>

# Step 4: Extract free symbols \[Back to [top](#toc)\]
$$\label{list_free_symbols}$$

By ''free symbols'' we mean the variables in the right-hand sides.  We first create a list of all such terms (using SymPy's built-in free_symbol attribute), including duplicates, and then strip the duplicates.  We then remove input constants from the symbol list.

In [4]:
# Step 4.a: Prepare array of "free symbols" in the right-hand side expressions
full_symbol_list_with_dups = []
for i in range(len(lr)):
    for variable in rhss[i].free_symbols:
        full_symbol_list_with_dups.append(variable)

# Step 4.b: Remove duplicate free symbols
full_symbol_list = superfast_uniq(full_symbol_list_with_dups)

# Step 4.c: Remove input constants from symbol list
for inputconst in input_constants:
    for symbol in full_symbol_list:
        if str(symbol) == str(inputconst):
            full_symbol_list.remove(symbol)

<a id='convert_to_func'></a>

# Step 5: Convert variables to function notation; e.g., `var` goes to `var(xx)` \[Back to [top](#toc)\]
$$\label{convert_to_func}$$

In order to compute the partial derivative of each right-hand side, we mark each variable (left-hand side) and each free symbol (in right-hand sides) as a function with argument $\texttt{xx}$.

In [5]:
# Step 5.a: Convert each left-hand side to function notation
#   while separating and simplifying left- and right-hand sides
xx = sp.Symbol('xx',real=True)
func = []
for i in range(len(lr)):
    func.append(sp.sympify(sp.Function(lr[i].lhs)(xx)))

# Step 5.b: Mark each free variable as a function with argument xx
full_function_list = []
for symb in full_symbol_list:
    func = sp.sympify(sp.Function(str(symb))(xx))
    full_function_list.append(func)
    for i in range(len(rhss)):
        for var in rhss[i].free_symbols:
            if str(var) == str(symb):
                rhss[i] = rhss[i].subs(var,func)

<a id='differentiate'></a>

# Step 6: Differentiate with respect to `xx` \[Back to [top](#toc)\]
$$\label{differentiate}$$

Now we differentiate the right-hand expressions with respect to `xx`.  We use the SymPy $\texttt{diff}$ command, differentiating with respect to $\texttt{xx}$.  After so doing, we remove $\texttt{(xx)}$ and "Derivative" (which is output by $\texttt{diff}$), and use "prm" suffix to denote the derivative with respect to $\texttt{xx}$.

In [6]:
# Step 6: Use SymPy's diff function to differentiate right-hand sides with respect to xx
#   and append "prm" notation to left-hand sides
lhss_deriv = []
rhss_deriv = []
for i in range(len(rhss)):
    lhss_deriv.append(sp.sympify(str(lhss[i])+"prm"))
    newrhs = sp.sympify(str(sp.diff(rhss[i],xx)).replace("(xx)","").replace(", xx","prm").replace("Derivative",""))
    rhss_deriv.append(newrhs)

<a id='remove_zeros'></a>

# Step 7: Remove derivatives (of constants) that evaluate to zero, simplifying derivative expressions \[Back to [top](#toc)\]
$$\label{remove_zeros}$$

We declare a function to simply the derivative expressions.  In particular, we want to remove terms equal to zero.

In [7]:
# Step 7.a: Define derivative simplification function
def simplify_deriv(lhss_deriv,rhss_deriv):
    # Copy expressions into another array
    lhss_deriv_simp = []
    rhss_deriv_simp = []
    for i in range(len(rhss_deriv)):
        lhss_deriv_simp.append(lhss_deriv[i])
        rhss_deriv_simp.append(rhss_deriv[i])
    # If a right-hand side is 0, substitute value 0 for the corresponding left-hand side in later terms
    for i in range(len(rhss_deriv_simp)):
        if rhss_deriv_simp[i] == 0:
            for j in range(i+1,len(rhss_deriv_simp)):
                for var in rhss_deriv_simp[j].free_symbols:
                    if str(var) == str(lhss_deriv_simp[i]):
                        rhss_deriv_simp[j] = rhss_deriv_simp[j].subs(var,0)
    zero_elements_to_remove = []
    # Create array of indices for expressions that are zero
    for i in range(len(rhss_deriv_simp)):
        if rhss_deriv_simp[i] == sp.sympify(0):
            zero_elements_to_remove.append(i)

    # When removing terms that are zero, we need to take into account their new index (after each removal)
    count = 0
    for i in range(len(zero_elements_to_remove)):
        del lhss_deriv_simp[zero_elements_to_remove[i]+count]
        del rhss_deriv_simp[zero_elements_to_remove[i]+count]
        count -= 1
    return lhss_deriv_simp,rhss_deriv_simp

# Step 7.b: Call the simplication function and then copy results
lhss_deriv_simp,rhss_deriv_simp = simplify_deriv(lhss_deriv,rhss_deriv)
lhss_deriv = lhss_deriv_simp
rhss_deriv = rhss_deriv_simp

<a id='partial_derivative'></a>

# Step 8: Simplify derivatives with respect to a specific variable \[Back to [top](#toc)\]
$$\label{partial_derivative}$$

In [Step 6](#differentiate) we took a generic derivative of each expression, assuming all variables were functions of `xx`.  We now define a function that will select a specific dynamic variable (element of `dynamic_variables`) and set the derivative of the variable to 1 and all others to 0.

In [8]:
# Step 8.a: Define onevar derivative function
def deriv_onevar(lhss_deriv,rhss_deriv,variable_list,index):
    # Denote each variable with prm
    variableprm_list = []
    for variable in variable_list:
        variableprm_list.append(str(variable)+"prm")

    # Copy expressions into another array
    lhss_deriv_new = []
    rhss_deriv_new = []
    for i in range(len(rhss_deriv)):
        lhss_deriv_new.append(lhss_deriv[i])
        rhss_deriv_new.append(rhss_deriv[i])
    # For each free symbol's derivative, replace it with:
    #   1, if we are differentiating with respect to the variable, or
    #   0, if we are note differentiating with respect to that variable
    for i in range(len(rhss_deriv_new)):
        for var in variableprm_list:
            if variableprm_list.index(str(var))==index:
                rhss_deriv_new[i] = rhss_deriv_new[i].subs(var,1)
            else:
                rhss_deriv_new[i] = rhss_deriv_new[i].subs(var,0)
    # Simplify derivative expressions again
    lhss_deriv_simp,rhss_deriv_simp = simplify_deriv(lhss_deriv_new,rhss_deriv_new)
    return lhss_deriv_simp,rhss_deriv_simp

# Step 8.b: Call the derivative function and populate dictionaries with the result
lhss_derivative = {}
rhss_derivative = {}
for index in range(len(dynamic_variables)):
    lhss_temp,rhss_temp = deriv_onevar(lhss_deriv,rhss_deriv,dynamic_variables,index)
    lhss_derivative[dynamic_variables[index]] = lhss_temp
    rhss_derivative[dynamic_variables[index]] = rhss_temp

<a id='store_results'></a>

# Step 9: Store partial derivatives to SymPy notebook `partial_derivatives.txt-VALIDATION.txt` \[Back to [top](#toc)\]
$$\label{store_results}$$

We write the resulting derivatives in SymPy syntax.  Each partial derivative is output in its own file, in a similar format to the input expressions.

In [9]:
# Step 9: Output original expression and each partial derivative expression in SymPy snytax
with open(os.path.join(inputdir,'partial_derivatives.txt-VALIDATION'), 'w') as output:
    for i in range(len(lr)):
        right_side = lr[i].rhs
        right_side_in_sp = right_side.replace("sqrt(","sp.sqrt(").replace("log(","sp.log(").replace("pi",
                                                "sp.pi").replace("sign(","sp.sign(").replace("Abs(",
                                                "sp.Abs(").replace("Rational(","sp.Rational(")
        output.write(str(lr[i].lhs)+" = "+right_side_in_sp)
    for var in dynamic_variables:
        for i in range(len(lhss_derivative[var])):
            right_side = str(rhss_derivative[var][i])
            right_side_in_sp = right_side.replace("sqrt(","sp.sqrt(").replace("log(","sp.log(").replace("pi",
                                                "sp.pi").replace("sign(","sp.sign(").replace("Abs(",
                                                "sp.Abs(").replace("Rational(","sp.Rational(").replace("prm",
                                                "prm_"+str(var))
            output.write(str(lhss_derivative[var][i]).replace("prm","prm_"+str(var))+" = "+right_side_in_sp+"\n")

<a id='code_validation'></a>

# Step 10: Validate against trusted `SEOBNR_Derivative_Routine` NRPy+ module \[Back to [top](#toc)\]
$$\label{code_validation}$$

We validate the output of this notebook against the output of the `SEOBNR_Derivative_Routine` NRPy+ module by comparing the output line-by-line.

In [10]:
values = {'m1': 1.3e+01, 'm2': 1.1e+01, 'eta': 2.482638888888889e-01, 'x': 1.658444292696035e+01, 'y': 0.0e+00,
          'z': 0.0e+00, 'px': -8.721133427338679e-04, 'py': 2.693195683074527e-01, 'pz': -1.307987305388598e-04,
          's1x': 2.934027777777778e-02, 's1y': -5.868055555555557e-02, 's1z': 8.802083333333334e-02,
          's2x': -6.302083333333333e-02, 's2y': 4.201388888888890e-02, 's2z': -2.100694444444445e-02,
          'KK': 3.913980338468737e-01, 'k0': -7.447639215330089e-01, 'k1': -6.380586501824999e-01,
          'd1v2': -7.476323019145448e+01, 'dheffSSv2': 2.105103187692902e+01, 'tortoise': 1,
          'EMgamma': 0.577215664901532860606512090082402431}
for i in range(len(rhss)):
    term = sp.sympify(str(rhss[i]).replace("(xx)",""))
    for variable in values:
        term = term.subs(variable, values[variable])
        print("I subbed in ",variable," and got ",term)
    rhss[i] = sp.sympify(term)
    for k in range(i):
        term = term.subs(lhss[k],rhss[k])
        print("I subbed in ",lhss[k]," which is now ",rhss[k]," and got ",term)
    rhss[i] = term.evalf()
print("Hreal = ",rhss[-1])

I subbed in  s1x  and got  s2x + 0.0293402777777778
I subbed in  tortoise  and got  s2x + 0.0293402777777778
I subbed in  py  and got  s2x + 0.0293402777777778
I subbed in  KK  and got  s2x + 0.0293402777777778
I subbed in  px  and got  s2x + 0.0293402777777778
I subbed in  k0  and got  s2x + 0.0293402777777778
I subbed in  y  and got  s2x + 0.0293402777777778
I subbed in  s1y  and got  s2x + 0.0293402777777778
I subbed in  d1v2  and got  s2x + 0.0293402777777778
I subbed in  z  and got  s2x + 0.0293402777777778
I subbed in  m1  and got  s2x + 0.0293402777777778
I subbed in  pz  and got  s2x + 0.0293402777777778
I subbed in  dheffSSv2  and got  s2x + 0.0293402777777778
I subbed in  EMgamma  and got  s2x + 0.0293402777777778
I subbed in  k1  and got  s2x + 0.0293402777777778
I subbed in  s2y  and got  s2x + 0.0293402777777778
I subbed in  m2  and got  s2x + 0.0293402777777778
I subbed in  s2x  and got  -0.0336805555555555
I subbed in  s1z  and got  -0.0336805555555555
I subbed in  s2z  

I subbed in  KK  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  px  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  k0  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  y  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  s1y  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  d1v2  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  z  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  m1  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  pz  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  dheffSSv2  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  EMgamma  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  k1  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  s2y  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  m2  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  s2x  and got  m1overm2*s2z + m2overm1*s1z
I subbed in  s1z  and got  m1overm2*s2z + 0.0880208333333333*m2overm1
I subbed in  s2z  and got  -0.0210069444444444*m1overm2 + 0.0880208333333333*m2overm1
I subbed in  eta  a

I subbed in  m1overm2  which is now  1.18181818181818  and got  u*u4
I subbed in  sigmaStar0  which is now  -0.0496527777777778  and got  u*u4
I subbed in  sigmaStar1  which is now  0  and got  u*u4
I subbed in  sigmaStar2  which is now  0.0496527777777778  and got  u*u4
I subbed in  s1dots1  which is now  0.0120519266010802  and got  u*u4
I subbed in  s2dots2  which is now  0.00617808400848766  and got  u*u4
I subbed in  r2  which is now  275.043747197605  and got  u*u4
I subbed in  r  which is now  16.5844429269603  and got  u*u4
I subbed in  u  which is now  0.0602974730236105  and got  0.0602974730236105*u4
I subbed in  u2  which is now  0.00363578525303304  and got  0.0602974730236105*u4
I subbed in  u3  which is now  0.000219228663214401  and got  0.0602974730236105*u4
I subbed in  u4  which is now  1.32189344061725e-5  and got  7.97068340757064e-7
I subbed in  s1x  and got  eta*u3
I subbed in  tortoise  and got  eta*u3
I subbed in  py  and got  eta*u3
I subbed in  KK  and got  e

I subbed in  m2overm1  which is now  0.846153846153846  and got  0
I subbed in  m1overm2  which is now  1.18181818181818  and got  0
I subbed in  sigmaStar0  which is now  -0.0496527777777778  and got  0
I subbed in  sigmaStar1  which is now  0  and got  0
I subbed in  sigmaStar2  which is now  0.0496527777777778  and got  0
I subbed in  s1dots1  which is now  0.0120519266010802  and got  0
I subbed in  s2dots2  which is now  0.00617808400848766  and got  0
I subbed in  r2  which is now  275.043747197605  and got  0
I subbed in  r  which is now  16.5844429269603  and got  0
I subbed in  u  which is now  0.0602974730236105  and got  0
I subbed in  u2  which is now  0.00363578525303304  and got  0
I subbed in  u3  which is now  0.000219228663214401  and got  0
I subbed in  u4  which is now  1.32189344061725e-5  and got  0
I subbed in  u5  which is now  7.97068340757064e-7  and got  0
I subbed in  etau3  which is now  5.44265604855196e-5  and got  0
I subbed in  etau4  which is now  3.281

I subbed in  etau3  which is now  5.44265604855196e-5  and got  -0.0496527777777778
I subbed in  etau4  which is now  3.28178406264352e-6  and got  -0.0496527777777778
I subbed in  nx  which is now  1.00000000000000  and got  -0.0496527777777778
I subbed in  ny  which is now  0  and got  -0.0496527777777778
I subbed in  nz  which is now  0  and got  -0.0496527777777778
I subbed in  sKerrUSCOREx  which is now  -0.0336805555555555  and got  -0.0496527777777778
I subbed in  sKerrUSCOREy  which is now  -0.0166666666666667  and got  -0.0496527777777778
I subbed in  sKerrUSCOREz  which is now  0.0670138888888889  and got  -0.0496527777777778
I subbed in  s1x  and got  sigmaStar1
I subbed in  tortoise  and got  sigmaStar1
I subbed in  py  and got  sigmaStar1
I subbed in  KK  and got  sigmaStar1
I subbed in  px  and got  sigmaStar1
I subbed in  k0  and got  sigmaStar1
I subbed in  y  and got  sigmaStar1
I subbed in  s1y  and got  sigmaStar1
I subbed in  d1v2  and got  sigmaStar1
I subbed in  z

...

I subbed in  b3  which is now  0  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  bb3  which is now  0  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  ww  which is now  2.54840219684629  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  B  which is now  15.5539985357214  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  sqrtdeltaT  which is now  15.5539985357214  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  sqrtdeltaR  which is now  15.6171111890046  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  deltaTsqrtdeltaR  which is now  3778.19883541342  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  sqrtdeltaTdeltaTsqrtdeltaR  which is now  58766.0991536846  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  invdeltaTsqrtdeltaTsqrtdeltaR  which is now  1.70166135646473e-5  and got  Hns + 21.051031876929*Hpt1 + Hs + Hss
I subbed in  invdeltaT  which is now  0.00413348049409784  and got  Hns + 21.05103

I subbed in  sMultiplier2pt5  which is now  -5.97732450275851e-6  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  sMultiplier2pt4  which is now  0.000373566336837383  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  sMultiplier2pt3  which is now  -0.000897593468580808  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  sMultiplier2pt2  which is now  -0.00228810933103054  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  sMultiplier2pt1  which is now  -0.0380768063686654  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  sMultiplier2  which is now  -0.00945309602555408  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  deltaSigmaStarUSCOREx2  which is now  -0.000940063306777039  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  deltaSigmaStarUSCOREy2  which is now  0.000248862388615323  and got  21.051031876929*Hpt1 + Hs + Hss

I subbed in  HSONLpt2b  which is now  0.172400491164626  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  HSONLpt2a  which is now  0.765593369511266  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  HSONLpt2  which is now  0.0352029143595489  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  HSONLpt3c  which is now  0.169008920278324  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  HSONLpt3b  which is now  0.344039855967809  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  HSONLpt3a  which is now  5.35114344162669  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  HSONLpt3  which is now  0.516085085351283  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  HSONLpt4e  which is now  -0.0407597303078731  and got  21.051031876929*Hpt1 + Hs + Hss + 0.97140404658864
I subbed in  HSONLpt4d  which is now  -0.125183839076682  and go

I subbed in  expnusq  which is now  0.879573433903177  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  expMUsqexpnusq  which is now  241.922170966551  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  invexpnuexpMU  which is now  0.0642927740063017  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  invexpMU  which is now  0.0602973486797091  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  invexpMUsq  which is now  0.00363577025780242  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  expnuinvexpMU2  which is now  0.00340982809254024  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  invexpMUcubinvexpnu  which is now  0.000233753755523724  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  DD  which is now  1.00813176079554  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  deltaR  which is now  243.894161889731  and got  sqrt(0.4965277777777

I subbed in  sMultiplier2pt1  which is now  -0.0380768063686654  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  sMultiplier2  which is now  -0.00945309602555408  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  deltaSigmaStarUSCOREx2  which is now  -0.000940063306777039  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  deltaSigmaStarUSCOREy2  which is now  0.000248862388615323  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  deltaSigmaStarUSCOREz2  which is now  0.000442338529546394  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  deltaSigmaStarUSCOREx  which is now  -0.000803013573929651  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  deltaSigmaStarUSCOREy  which is now  0.000316680813117123  and got  sqrt(0.496527777777778*H + 0.503472222222222)
I subbed in  deltaSigmaStarUSCOREz  which is now  0.000169651947695405  and got  sqrt(0.496527777777778*H + 0.503472222222

In [11]:
print("Printing difference between notebook output and trusted NRPy+ module output...")
# Open the files to compare
file = 'partial_derivatives.txt'
outfile = 'partial_derivatives.txt-VALIDATION'

print("Checking file " + outfile)
with open(os.path.join(inputdir,file), "r") as file1, open(os.path.join(inputdir,outfile), "r") as file2:
    # Read the lines of each file
    file1_lines = file1.readlines()
    file2_lines = file2.readlines()
    # Compare right-hand sides of the expressions by computing the difference between them
    num_diffs = 0
    for i in range(len(file1_lines)):
        expr_new = sp.sympify(file1_lines[i].split("=")[1].replace("sp.",""))
        expr_validated = sp.sympify(file2_lines[i].split("=")[1].replace("sp.",""))
        difference = sp.simplify(expr_new - expr_validated)
        if difference != 0:
            num_diffs + 1
            print(difference)
    if num_diffs == 0:
        print("No difference. TEST PASSED!")
    else:
        print("ERROR: Disagreement found with the trusted file. See differences above.")
        sys.exit(1)

Printing difference between notebook output and trusted NRPy+ module output...
Checking file partial_derivatives.txt-VALIDATION
No difference. TEST PASSED!


<a id='latex_pdf_output'></a>

# Step 11: Output this notebook to $\LaTeX$-formatted PDF file \[Back to [top](#toc)\]
$$\label{latex_pdf_output}$$

The following code cell converts this Jupyter notebook into a proper, clickable $\LaTeX$-formatted PDF file. After the cell is successfully run, the generated PDF may be found in the root NRPy+ tutorial directory, with filename
[Tutorial-SEOBNR_Derivative_Routine.pdf](Tutorial-SEOBNR_Derivative_Routine.pdf) (Note that clicking on this link may not work; you may need to open the PDF file through another means.)

In [12]:
import cmdline_helper as cmd      # NRPy+: Multi-platform Python command-line interface

cmd.output_Jupyter_notebook_to_LaTeXed_PDF("NRPyPN_shortcuts",location_of_template_file=os.path.join(".."))

Notebook output to PDF is only supported on Linux systems, with pdflatex installed.
